In [1]:
import numpy as np
import trimesh
from matplotlib import pyplot as plt

Проверка наличия блендера на устройстве, чтобы использовать его движок в дальнейшем.

In [2]:
print(trimesh.interfaces.blender.exists)
engine = 'blender'

True


Загрузка моделей, где cube - это предпологаемая зона интереса(ЗИ), а ball - сфера, которая будет покрывать зону.

In [3]:
ball = trimesh.load_mesh('resources/ball.stl')
cube = trimesh.load_mesh('resources/cube.stl')
ball = ball.apply_scale(0.25)
# cube = cube.apply_scale(0.5)

Устанавливаем сферу в центр масс ЗИ.

In [4]:
center = cube.center_mass
translation = trimesh.transformations.translation_matrix(center)
ball.apply_transform(translation)

<trimesh.Trimesh(vertices.shape=(144, 3), faces.shape=(284, 3))>

Функция для расчета радиуса сферы.

In [5]:
def ball_radius(ball: trimesh.Trimesh) -> float:
    vertexes = trimesh.bounds.corners(ball.bounds)
    source = np.array(ball.center_mass)
    dest = np.array(vertexes[0])
    vec = dest - source
    return np.linalg.norm(vec) * (2 ** 0.5) / 2 / 1.25

Определяем матрицу трансформаций для перехода в целочисленную систему координат относительно центра масс ЗИ, чтобы удобнее далее работать со списком имеющихся шаров.

In [6]:
from typing import List, Dict

r = ball_radius(ball)
center = cube.center_mass
transform = np.matrix([[r, 0, 0, center[0]],
                      [0, r, 0, center[1]],
                      [0, 0, r, center[2]],
                      [0, 0, 0, 1]]
                     )

Функции для заливки и покрытия сферами ЗИ.

In [7]:
def check_size(x, y, z, size: list) -> bool:
    return x >= 0 and x < size[0] and y >= 0 and y < size[1] and z >= 0 and z < size[2]


def check_dict(balls_dict, x, y, z) -> str:
    if balls_dict.get(z):
        if balls_dict.get(z).get(y):
            if balls_dict.get(z).get(y).get(x):
                return "exist"
            else:
                return "x"
        else:
            return "y"
    return "z"


def fill_check(balls_dict: Dict[int, Dict[int, Dict[int, trimesh.Trimesh]]], x, y, z, tumor: trimesh.Trimesh, queue: List[np.ndarray]) -> None:
    check = check_dict(balls_dict, x, y, z)
    if check == "exist":
        return
    new_ball = ball.copy().apply_transform(trimesh.transformations.translation_matrix(np.array((transform @ np.vstack([x, y, z, 1])).T)[0][0:3]))
    if trimesh.boolean.difference([tumor, new_ball]).volume < tumor.volume:
        queue.append(np.array([x, y, z]))
    else:
        return
    if check == "x":
        balls_dict[z][y][x] = new_ball
    elif check == "y":
        balls_dict[z][y] = {x: new_ball}
    elif check == "z":
        balls_dict[z] = {y: {x: new_ball}}
    return           

Функция для генерации самих шариков.

In [8]:
def generate_balls(tumor: trimesh.Trimesh, ball: trimesh.Trimesh) -> list:
    translation_arr = [
        np.array([1, 0, 0]),
        np.array([-1, 0, 0]),
        np.array([0, 1, 0]),
        np.array([0, -1, 0]),
        np.array([0, 0, 1]),
        np.array([0, 0, -1])
    ]
    balls_dict = {}
    balls = []
    queue = []
    queue.append(np.array([0, 0, 0]))
    while(queue):
        print("number of points in queue:", len(queue))
        item = queue.pop()
        x = item[0]
        y = item[1]
        z = item[2]
        for arr in translation_arr:
            fill_check(balls_dict, x + arr[0], y + arr[1], z + arr[2], tumor, queue=queue)
    for zV in balls_dict.values():
        for yV in zV.values():
            for xV in yV.values():
                balls.append(xV)
    return balls

Функция, чтобы отобразить сгенерированные сферы. Возвращает сцену, которая содержит в себе все сферы.

In [9]:
def print_balls(balls: List[trimesh.Trimesh]) -> trimesh.scene.scene.Scene:
    scene = trimesh.Scene()
    for item in balls:
        scene.add_geometry(item)
    return scene

Генерируем сферы.

In [10]:
b = generate_balls(cube, ball)

number of points in queue: 1
number of points in queue: 6
number of points in queue: 11
number of points in queue: 15
number of points in queue: 18
number of points in queue: 20
number of points in queue: 23
number of points in queue: 26
number of points in queue: 29
number of points in queue: 32
number of points in queue: 36
number of points in queue: 40
number of points in queue: 44
number of points in queue: 48
number of points in queue: 49
number of points in queue: 51
number of points in queue: 54
number of points in queue: 57
number of points in queue: 60
number of points in queue: 62
number of points in queue: 65
number of points in queue: 67
number of points in queue: 70
number of points in queue: 73
number of points in queue: 76
number of points in queue: 79
number of points in queue: 81
number of points in queue: 83
number of points in queue: 86
number of points in queue: 89
number of points in queue: 91
number of points in queue: 93
number of points in queue: 95
number of po

In [11]:
print("Общее кол-во сфер:", len(b))

Общее кол-во сфер: 635


Отображение сфер.

In [12]:
scene = print_balls(b)
scene.show()

c:\users\andro\documents\pycharmprojects\bachelor\venv\lib\site-packages\IPython\core\display.py:419: UserWarning: Consider using IPython.display.IFrame instead
  warnings.warn("Consider using IPython.display.IFrame instead")


Демонстрация вычитанием, что сферы полностью покрыли ЗИ. (Должна быть пустота на сцене, а тип разницы должен быть class 'trimesh.scene.scene.Scene')

In [13]:
buff = [cube]
buff.extend(b)
diff = trimesh.boolean.difference(buff, engine='blender')
print("Результат операции пустота? -", type(diff) == trimesh.scene.scene.Scene)
diff.show()

Результат операции пустота? - False


Демонстрация, как ЗИ вычитается из всех сфер.

In [14]:
summ = trimesh.boolean.union(b, engine)
d = summ.difference(cube, engine)
d.show()